In [10]:
import pymongo
from pymongo import MongoClient
import pandas as pd
import numpy as np
from urllib.parse import quote_plus
from IPython.display import display, HTML
import warnings
warnings.filterwarnings("ignore")

In [11]:
username = quote_plus("balamariappan20")
password = quote_plus("Naruto@2024")
clustername = "airbnb.hrkwsrt.mongodb.net"
database_name = "sample_airbnb"
connection_string = f"mongodb+srv://{username}:{password}@{clustername}/?retryWrites=true&w=majority&appName=airbnb"
client = MongoClient(connection_string)
db = client['sample_airbnb']
collection = db['listingsAndReviews']

In [17]:
airbnb_data = list(collection.find({}, {"_id": 1, "listing_url": 1, "name": 1, 'property_type': 1, 'room_type': 1, 'bed_type': 1, 'minimum_nights': 1, 'maximum_nights': 1, 'cancellation_policy': 1, 'accommodates': 1, 'bedrooms': 1, 'beds': 1, 'number_of_reviews': 1, 'bathrooms': 1, 'price': 1, 'extra_people': 1, 'guests_included': 1, 'images.picture_url': 1, 'review_scores': 1, 'cleaning_fee': 1}))
df = pd.DataFrame(airbnb_data)

def image_formatter(image_dict):
    if 'picture_url' in image_dict:
        return f'<img src="{image_dict["picture_url"]}" width="200px" height:"200px"/>'
    else:
        return ''

df['Image'] = df['images'].apply(image_formatter)

df.drop(columns=['images'], inplace=True)

display(HTML(df.to_html(escape=False)))

In [18]:
df["review_scores"] = df["review_scores"].apply(lambda x: x.get("review_scores_rating", 0) if isinstance(x, dict) else 0)
df.describe().T

count       mean        std  min  25%   50%   75%    max
accommodates       5555.0   3.505851   2.297019  1.0  2.0   3.0   4.0   16.0
bedrooms           5550.0   1.411712   1.041942  0.0  1.0   1.0   2.0   20.0
beds               5542.0   2.071454   1.619660  0.0  1.0   2.0   3.0   25.0
number_of_reviews  5555.0  27.606481  49.798376  0.0  1.0   5.0  32.0  533.0
review_scores      5555.0  68.395680  41.829834  0.0  0.0  92.0  98.0  100.0

In [19]:
df.isnull().sum()

_id                       0
listing_url               0
name                      0
property_type             0
room_type                 0
bed_type                  0
minimum_nights            0
maximum_nights            0
cancellation_policy       0
accommodates              0
bedrooms                  5
beds                     13
number_of_reviews         0
bathrooms                10
price                     0
cleaning_fee           1531
extra_people              0
guests_included           0
review_scores             0
Image                     0
dtype: int64

In [20]:
#HANDLINGNULL VALUES

In [21]:
df["beds"].fillna(0,inplace= True)
df["bedrooms"].fillna(0,inplace= True)
df["bathrooms"].fillna(0,inplace= True)
df["cleaning_fee"].fillna(0,inplace= True)

In [22]:
df.isnull().sum()

_id                    0
listing_url            0
name                   0
property_type          0
room_type              0
bed_type               0
minimum_nights         0
maximum_nights         0
cancellation_policy    0
accommodates           0
bedrooms               0
beds                   0
number_of_reviews      0
bathrooms              0
price                  0
cleaning_fee           0
extra_people           0
guests_included        0
review_scores          0
Image                  0
dtype: int64

In [23]:
df.head(2)

_id                            listing_url  \
0  10006546  https://www.airbnb.com/rooms/10006546   
1  10009999  https://www.airbnb.com/rooms/10009999   

                           name property_type        room_type  bed_type  \
0       Ribeira Charming Duplex         House  Entire home/apt  Real Bed   
1  Horto flat with small garden     Apartment  Entire home/apt  Real Bed   

  minimum_nights maximum_nights cancellation_policy  accommodates  bedrooms  \
0              2             30            moderate             8       3.0   
1              2           1125            flexible             4       1.0   

   beds  number_of_reviews bathrooms   price cleaning_fee extra_people  \
0   5.0                 51       1.0   80.00        35.00        15.00   
1   2.0                  0       1.0  317.00       187.00         0.00   

  guests_included  review_scores  \
0               6             89   
1               1              0   

                                               Image  
0  <img src="https://a0.muscache.com/im/pictures/...  
1  <img src="https://a0.muscache.com/im/pictures/...

In [24]:
df.dtypes

_id                     object
listing_url             object
name                    object
property_type           object
room_type               object
bed_type                object
minimum_nights          object
maximum_nights          object
cancellation_policy     object
accommodates             int64
bedrooms               float64
beds                   float64
number_of_reviews        int64
bathrooms               object
price                   object
cleaning_fee            object
extra_people            object
guests_included         object
review_scores            int64
Image                   object
dtype: object

In [25]:
df["minimum_nights"]= df["minimum_nights"].astype(int)
df["maximum_nights"]= df["maximum_nights"].astype(int)
df["bedrooms"]= df["bedrooms"].astype(int)
df["beds"]= df["beds"].astype(int)
df["bathrooms"]= df["bathrooms"].astype(str).astype(float).astype(int)
df["price"]= df["price"].astype(str).astype(float).astype(int)
df["extra_people"]= df["extra_people"].astype(str).astype(float).astype(int)
df["guests_included"]= df["guests_included"].astype(str).astype(float).astype(int)
df["cleaning_fee"]= df["cleaning_fee"].astype(str).astype(float).astype(int)

In [26]:
#HOST DETAILS

In [27]:
host_data = list(collection.find({}, {"_id": 1, "host": 1}))
host_columns = {
    '_id': [item['_id'] for item in host_data],
    'host_id': [item['host']['host_id'] for item in host_data],
    'host_url': [item['host']['host_url'] for item in host_data],
    'host_name': [item['host']['host_name'] for item in host_data],
    'host_location': [item['host']['host_location'] for item in host_data],
    'host_response_time': [item['host'].get('host_response_time') for item in host_data],
    'host_thumbnail_url': [item['host']['host_thumbnail_url'] for item in host_data],
    'host_picture_url': [item['host']['host_picture_url'] for item in host_data],
    'host_neighbourhood': [item['host']['host_neighbourhood'] for item in host_data],
    'host_response_rate': [item['host'].get('host_response_rate') for item in host_data],
    'host_is_superhost': [item['host']['host_is_superhost'] for item in host_data],
    'host_has_profile_pic': [item['host']['host_has_profile_pic'] for item in host_data],
    'host_identity_verified': [item['host']['host_identity_verified'] for item in host_data],
    'host_listings_count': [item['host']['host_listings_count'] for item in host_data],
    'host_total_listings_count': [item['host']['host_total_listings_count'] for item in host_data],
    'host_verifications': [item['host']['host_verifications'] for item in host_data]
}
df_host = pd.DataFrame(host_columns)
df_host

_id   host_id                                    host_url  \
0     10006546  51399391  https://www.airbnb.com/users/show/51399391   
1     10009999   1282196   https://www.airbnb.com/users/show/1282196   
2      1001265   5448114   https://www.airbnb.com/users/show/5448114   
3     10021707  11275734  https://www.airbnb.com/users/show/11275734   
4     10030955  51496939  https://www.airbnb.com/users/show/51496939   
...        ...       ...                                         ...   
5550   9983221  37776205  https://www.airbnb.com/users/show/37776205   
5551   9985696  51303748  https://www.airbnb.com/users/show/51303748   
5552   9987200  51314789  https://www.airbnb.com/users/show/51314789   
5553   9990304  51013381  https://www.airbnb.com/users/show/51013381   
5554   9993190  51013381  https://www.airbnb.com/users/show/51013381   

           host_name                                    host_location  \
0        Ana&Gonçalo                  Porto, Porto District, Portugal   
1              Ynaie  Rio de Janeiro, State of Rio de Janeiro, Brazil   
2              David                  Honolulu, Hawaii, United States   
3               Josh                New York, New York, United States   
4              Livia                                               BR   
...              ...                                              ...   
5550             Ana                                         Portugal   
5551            Eren                       Kadikoy, Çanakkale, Turkey   
5552          Dumont  Rio de Janeiro, State of Rio de Janeiro, Brazil   
5553  Coconut Condos                   Lahaina, Hawaii, United States   
5554  Coconut Condos                   Lahaina, Hawaii, United States   

     host_response_time                                 host_thumbnail_url  \
0        within an hour  https://a0.muscache.com/im/pictures/fab79f25-2...   
1                  None  https://a0.muscache.com/im/pictures/9681e3cc-4...   
2        within an hour  https://a0.muscache.com/im/users/5448114/profi...   
3                  None  https://a0.muscache.com/im/users/11275734/prof...   
4                  None  https://a0.muscache.com/im/pictures/b7911710-9...   
...                 ...                                                ...   
5550     within an hour  https://a0.muscache.com/im/users/37776205/prof...   
5551               None  https://a0.muscache.com/im/pictures/89a1b839-2...   
5552     within an hour  https://a0.muscache.com/im/pictures/65582ca0-8...   
5553     within an hour  https://a0.muscache.com/im/pictures/fa071e13-8...   
5554     within an hour  https://a0.muscache.com/im/pictures/fa071e13-8...   

                                       host_picture_url host_neighbourhood  \
0     https://a0.muscache.com/im/pictures/fab79f25-2...                      
1     https://a0.muscache.com/im/pictures/9681e3cc-4...    Jardim Botânico   
2     https://a0.muscache.com/im/users/5448114/profi...            Waikiki   
3     https://a0.muscache.com/im/users/11275734/prof...           Bushwick   
4     https://a0.muscache.com/im/pictures/b7911710-9...              Lagoa   
...                                                 ...                ...   
5550  https://a0.muscache.com/im/users/37776205/prof...                      
5551  https://a0.muscache.com/im/pictures/89a1b839-2...                      
5552  https://a0.muscache.com/im/pictures/65582ca0-8...         Copacabana   
5553  https://a0.muscache.com/im/pictures/fa071e13-8...                      
5554  https://a0.muscache.com/im/pictures/fa071e13-8...                      

      host_response_rate  host_is_superhost  host_has_profile_pic  \
0                  100.0              False                  True   
1                    NaN              False                  True   
2                   98.0              False                  True   
3                    NaN              False                  True   
4                    NaN              False       

In [28]:
nan_values = df_host.isnull().sum()
none_values = df_host.isna().sum()
empty_string_values = (df_host == '').sum()
missing_values = nan_values + none_values + empty_string_values
print("Total missing values by column:")
print(missing_values)


Total missing values by column:
_id                             0
host_id                         0
host_url                        0
host_name                       0
host_location                   8
host_response_time           2776
host_thumbnail_url              0
host_picture_url                0
host_neighbourhood           1923
host_response_rate           2776
host_is_superhost               0
host_has_profile_pic            0
host_identity_verified          0
host_listings_count             0
host_total_listings_count       0
host_verifications              0
dtype: int64


In [29]:
#HANDLINGNULL VALUES_FOR_HOST

In [30]:
df_host["host_response_time"].fillna(0, inplace=True)
df_host["host_neighbourhood"] = df_host["host_neighbourhood"].replace({'': "Not Specified"})
df_host["host_response_rate"].fillna(0, inplace=True)
df_host["host_location"] = df_host["host_location"].replace({'': "Not Specified"})

In [31]:
nan_values = df_host.isnull().sum()
none_values = df_host.isna().sum()
empty_string_values = (df_host == '').sum()
missing_values = nan_values + none_values + empty_string_values
print("Total missing values by column:")
print(missing_values)

Total missing values by column:
_id                          0
host_id                      0
host_url                     0
host_name                    0
host_location                0
host_response_time           0
host_thumbnail_url           0
host_picture_url             0
host_neighbourhood           0
host_response_rate           0
host_is_superhost            0
host_has_profile_pic         0
host_identity_verified       0
host_listings_count          0
host_total_listings_count    0
host_verifications           0
dtype: int64


In [32]:
df_host["host_is_superhost"]= df_host["host_is_superhost"].map({False: "No", True: "Yes"})
df_host["host_has_profile_pic"]= df_host["host_has_profile_pic"].map({False: "No", True: "Yes"})
df_host["host_identity_verified"]= df_host["host_identity_verified"].map({False: "No", True: "Yes"})

In [33]:
df_host

_id   host_id                                    host_url  \
0     10006546  51399391  https://www.airbnb.com/users/show/51399391   
1     10009999   1282196   https://www.airbnb.com/users/show/1282196   
2      1001265   5448114   https://www.airbnb.com/users/show/5448114   
3     10021707  11275734  https://www.airbnb.com/users/show/11275734   
4     10030955  51496939  https://www.airbnb.com/users/show/51496939   
...        ...       ...                                         ...   
5550   9983221  37776205  https://www.airbnb.com/users/show/37776205   
5551   9985696  51303748  https://www.airbnb.com/users/show/51303748   
5552   9987200  51314789  https://www.airbnb.com/users/show/51314789   
5553   9990304  51013381  https://www.airbnb.com/users/show/51013381   
5554   9993190  51013381  https://www.airbnb.com/users/show/51013381   

           host_name                                    host_location  \
0        Ana&Gonçalo                  Porto, Porto District, Portugal   
1              Ynaie  Rio de Janeiro, State of Rio de Janeiro, Brazil   
2              David                  Honolulu, Hawaii, United States   
3               Josh                New York, New York, United States   
4              Livia                                               BR   
...              ...                                              ...   
5550             Ana                                         Portugal   
5551            Eren                       Kadikoy, Çanakkale, Turkey   
5552          Dumont  Rio de Janeiro, State of Rio de Janeiro, Brazil   
5553  Coconut Condos                   Lahaina, Hawaii, United States   
5554  Coconut Condos                   Lahaina, Hawaii, United States   

     host_response_time                                 host_thumbnail_url  \
0        within an hour  https://a0.muscache.com/im/pictures/fab79f25-2...   
1                     0  https://a0.muscache.com/im/pictures/9681e3cc-4...   
2        within an hour  https://a0.muscache.com/im/users/5448114/profi...   
3                     0  https://a0.muscache.com/im/users/11275734/prof...   
4                     0  https://a0.muscache.com/im/pictures/b7911710-9...   
...                 ...                                                ...   
5550     within an hour  https://a0.muscache.com/im/users/37776205/prof...   
5551                  0  https://a0.muscache.com/im/pictures/89a1b839-2...   
5552     within an hour  https://a0.muscache.com/im/pictures/65582ca0-8...   
5553     within an hour  https://a0.muscache.com/im/pictures/fa071e13-8...   
5554     within an hour  https://a0.muscache.com/im/pictures/fa071e13-8...   

                                       host_picture_url host_neighbourhood  \
0     https://a0.muscache.com/im/pictures/fab79f25-2...      Not Specified   
1     https://a0.muscache.com/im/pictures/9681e3cc-4...    Jardim Botânico   
2     https://a0.muscache.com/im/users/5448114/profi...            Waikiki   
3     https://a0.muscache.com/im/users/11275734/prof...           Bushwick   
4     https://a0.muscache.com/im/pictures/b7911710-9...              Lagoa   
...                                                 ...                ...   
5550  https://a0.muscache.com/im/users/37776205/prof...      Not Specified   
5551  https://a0.muscache.com/im/pictures/89a1b839-2...      Not Specified   
5552  https://a0.muscache.com/im/pictures/65582ca0-8...         Copacabana   
5553  https://a0.muscache.com/im/pictures/fa071e13-8...      Not Specified   
5554  https://a0.muscache.com/im/pictures/fa071e13-8...      Not Specified   

      host_response_rate host_is_superhost host_has_profile_pic  \
0                  100.0                No                  Yes   
1                    0.0                No                  Yes   
2                   98.0                No                  Yes   
3                    0.0                No                  Yes   
4                    0.0                No                  

In [34]:
#ADDRESS

In [35]:
address_data = list(collection.find({}, {"_id": 1, "address": 1}))

address_columns = [{
    '_id': item['_id'],
    'street': item.get('address', {}).get('street'),
    'suburb': item.get('address', {}).get('suburb'),
    'government_area': item.get('address', {}).get('government_area'),
    'market': item.get('address', {}).get('market'),
    'country': item.get('address', {}).get('country'),
    'country_code': item.get('address', {}).get('country_code'),
    'location_type': item.get('address', {}).get('location', {}).get('type'),
    'longitude': item.get('address', {}).get('location', {}).get('coordinates', [])[0],
    'latitude': item.get('address', {}).get('location', {}).get('coordinates', [])[1],
    'is_location_exact': item.get('address', {}).get('location', {}).get('is_location_exact')
} for item in address_data]
df_address = pd.DataFrame(address_columns)
df_address

_id                                  street           suburb  \
0     10006546                  Porto, Porto, Portugal                    
1     10009999  Rio de Janeiro, Rio de Janeiro, Brazil  Jardim Botânico   
2      1001265             Honolulu, HI, United States            Oʻahu   
3     10021707             Brooklyn, NY, United States         Brooklyn   
4     10030955  Rio de Janeiro, Rio de Janeiro, Brazil            Lagoa   
...        ...                                     ...              ...   
5550   9983221                  Porto, Porto, Portugal                    
5551   9985696               Kadıköy, İstanbul, Turkey             Moda   
5552   9987200  Rio de Janeiro, Rio de Janeiro, Brazil       Copacabana   
5553   9990304              Lahaina, HI, United States             Maui   
5554   9993190              Lahaina, HI, United States          Lahaina   

                                        government_area          market  \
0     Cedofeita, Ildefonso, Sé, Miragaia, Nicolau, V...           Porto   
1                                       Jardim Botânico  Rio De Janeiro   
2                                  Primary Urban Center            Oahu   
3                                              Bushwick        New York   
4                                                 Lagoa  Rio De Janeiro   
...                                                 ...             ...   
5550  Cedofeita, Ildefonso, Sé, Miragaia, Nicolau, V...           Porto   
5551                                            Kadikoy        Istanbul   
5552                                         Copacabana  Rio De Janeiro   
5553                                            Lahaina            Maui   
5554                                            Lahaina            Maui   

            country country_code location_type   longitude   latitude  \
0          Portugal           PT         Point   -8.613080  41.141300   
1            Brazil           BR         Point  -43.230750 -22.966254   
2     United States           US         Point -157.839190  21.286340   
3     United States           US         Point  -73.936150  40.697910   
4            Brazil           BR         Point  -43.205047 -22.971951   
...             ...          ...           ...         ...        ...   
5550       Portugal           PT         Point   -8.616930  41.151370   
5551         Turkey           TR         Point   29.030790  40.985630   
5552         Brazil           BR         Point  -43.176533 -22.961076   
5553  United States           US         Point -156.676460  20.875610   
5554  United States           US         Point -156.667520  20.858940   

      is_location_exact  
0                 False  
1                  True  
2                  True  
3                  True  
4                  True  
...                 ...  
5550              False  
5551              False  
5552               True  
5553              False  
5554              False  

[5555 rows x 11 columns]

In [36]:
nan_values = df_address.isnull().sum()
none_values = df_address.isna().sum()
empty_string_values = (df_address == '').sum()
missing_values = nan_values + none_values + empty_string_values
print("Total missing values by column:")
print(missing_values)

Total missing values by column:
_id                    0
street                 0
suburb               887
government_area        0
market                 6
country                0
country_code           0
location_type          0
longitude              0
latitude               0
is_location_exact      0
dtype: int64


In [37]:
df_address["suburb"] = df_address["suburb"].replace({'': "Not Specified"})
df_address["market"] = df_address["market"].replace({'': "Not Specified"})
df_address["is_location_exact"]= df_address["is_location_exact"].map({False: "No", True: "Yes"})

In [38]:
df_address

_id                                  street           suburb  \
0     10006546                  Porto, Porto, Portugal    Not Specified   
1     10009999  Rio de Janeiro, Rio de Janeiro, Brazil  Jardim Botânico   
2      1001265             Honolulu, HI, United States            Oʻahu   
3     10021707             Brooklyn, NY, United States         Brooklyn   
4     10030955  Rio de Janeiro, Rio de Janeiro, Brazil            Lagoa   
...        ...                                     ...              ...   
5550   9983221                  Porto, Porto, Portugal    Not Specified   
5551   9985696               Kadıköy, İstanbul, Turkey             Moda   
5552   9987200  Rio de Janeiro, Rio de Janeiro, Brazil       Copacabana   
5553   9990304              Lahaina, HI, United States             Maui   
5554   9993190              Lahaina, HI, United States          Lahaina   

                                        government_area          market  \
0     Cedofeita, Ildefonso, Sé, Miragaia, Nicolau, V...           Porto   
1                                       Jardim Botânico  Rio De Janeiro   
2                                  Primary Urban Center            Oahu   
3                                              Bushwick        New York   
4                                                 Lagoa  Rio De Janeiro   
...                                                 ...             ...   
5550  Cedofeita, Ildefonso, Sé, Miragaia, Nicolau, V...           Porto   
5551                                            Kadikoy        Istanbul   
5552                                         Copacabana  Rio De Janeiro   
5553                                            Lahaina            Maui   
5554                                            Lahaina            Maui   

            country country_code location_type   longitude   latitude  \
0          Portugal           PT         Point   -8.613080  41.141300   
1            Brazil           BR         Point  -43.230750 -22.966254   
2     United States           US         Point -157.839190  21.286340   
3     United States           US         Point  -73.936150  40.697910   
4            Brazil           BR         Point  -43.205047 -22.971951   
...             ...          ...           ...         ...        ...   
5550       Portugal           PT         Point   -8.616930  41.151370   
5551         Turkey           TR         Point   29.030790  40.985630   
5552         Brazil           BR         Point  -43.176533 -22.961076   
5553  United States           US         Point -156.676460  20.875610   
5554  United States           US         Point -156.667520  20.858940   

     is_location_exact  
0                   No  
1                  Yes  
2                  Yes  
3                  Yes  
4                  Yes  
...                ...  
5550                No  
5551                No  
5552               Yes  
5553                No  
5554                No  

[5555 rows x 11 columns]

In [39]:
#Availiblity

In [40]:
availability_data = list(collection.find({}, {"_id": 1, "availability": 1}))

availability_columns = {
    '_id': [item['_id'] for item in availability_data],
    'availability_30': [item.get('availability', {}).get('availability_30') for item in availability_data],
    'availability_60': [item.get('availability', {}).get('availability_60') for item in availability_data],
    'availability_90': [item.get('availability', {}).get('availability_90') for item in availability_data],
    'availability_365': [item.get('availability', {}).get('availability_365') for item in availability_data]
}

df_availability = pd.DataFrame(availability_columns)
df_availability

_id  availability_30  availability_60  availability_90  \
0     10006546               28               47               74   
1     10009999                0                0                0   
2      1001265               16               46               76   
3     10021707                0                0                0   
4     10030955               28               58               88   
...        ...              ...              ...              ...   
5550   9983221               26               51               77   
5551   9985696               30               60               90   
5552   9987200                7               29               53   
5553   9990304                8               20               26   
5554   9993190                0                8               31   

      availability_365  
0                  239  
1                    0  
2                  343  
3                    0  
4                  363  
...                ...  
5550               300  
5551               365  
5552                53  
5553               243  
5554               258  

[5555 rows x 5 columns]

In [41]:
df_availability.isnull().sum()

_id                 0
availability_30     0
availability_60     0
availability_90     0
availability_365    0
dtype: int64

In [42]:
#Amenities

In [43]:
amenities_data = list(collection.find({}, {"_id": 1, "amenities": 1}))
df_amenities = pd.DataFrame(amenities_data)
df_amenities

_id                                          amenities
0     10006546  [TV, Cable TV, Wifi, Kitchen, Paid parking off...
1     10009999  [Wifi, Wheelchair accessible, Kitchen, Free pa...
2      1001265  [TV, Cable TV, Wifi, Air conditioning, Pool, K...
3     10021707  [Internet, Wifi, Air conditioning, Kitchen, Bu...
4     10030955  [TV, Cable TV, Internet, Wifi, Air conditionin...
...        ...                                                ...
5550   9983221  [TV, Cable TV, Internet, Wifi, Kitchen, Paid p...
5551   9985696  [TV, Cable TV, Internet, Wifi, Kitchen, Buzzer...
5552   9987200  [TV, Cable TV, Wifi, Air conditioning, Pool, G...
5553   9990304  [TV, Cable TV, Wifi, Air conditioning, Wheelch...
5554   9993190  [TV, Wifi, Air conditioning, Pool, Kitchen, Fr...

[5555 rows x 2 columns]

In [44]:
df_amenities.isnull().sum()

_id          0
amenities    0
dtype: int64

In [45]:
df_amenities.dtypes

_id          object
amenities    object
dtype: object

In [46]:
#Merging the All DataFrames

In [48]:
merged_df = pd.merge(df, df_host, on="_id", suffixes=('_df', '_host'))
merged_df = pd.merge(merged_df, df_address, on="_id", suffixes=('_merged', '_address'))
merged_df = pd.merge(merged_df, df_availability, on="_id", suffixes=('_merged', '_availability'))
merged_df = pd.merge(merged_df, df_amenities, on="_id", suffixes=('_merged', '_amenities'))

In [50]:
merged_df.head(5)

_id                            listing_url  \
0  10006546  https://www.airbnb.com/rooms/10006546   
1  10009999  https://www.airbnb.com/rooms/10009999   
2   1001265   https://www.airbnb.com/rooms/1001265   
3  10021707  https://www.airbnb.com/rooms/10021707   
4  10030955  https://www.airbnb.com/rooms/10030955   

                               name property_type        room_type  bed_type  \
0           Ribeira Charming Duplex         House  Entire home/apt  Real Bed   
1      Horto flat with small garden     Apartment  Entire home/apt  Real Bed   
2  Ocean View Waikiki Marina w/prkg   Condominium  Entire home/apt  Real Bed   
3          Private Room in Bushwick     Apartment     Private room  Real Bed   
4       Apt Linda Vista Lagoa - Rio     Apartment     Private room  Real Bed   

   minimum_nights  maximum_nights          cancellation_policy  accommodates  \
0               2              30                     moderate             8   
1               2            1125                     flexible             4   
2               3             365  strict_14_with_grace_period             2   
3              14            1125                     flexible             1   
4               1            1125                     flexible             2   

   ...  country_code  location_type   longitude   latitude  is_location_exact  \
0  ...            PT          Point   -8.613080  41.141300                 No   
1  ...            BR          Point  -43.230750 -22.966254                Yes   
2  ...            US          Point -157.839190  21.286340                Yes   
3  ...            US          Point  -73.936150  40.697910                Yes   
4  ...            BR          Point  -43.205047 -22.971951                Yes   

   availability_30  availability_60  availability_90  availability_365  \
0               28               47               74               239   
1                0                0                0                 0   
2               16               46               76               343   
3                0                0                0                 0   
4               28               58               88               363   

                                           amenities  
0  [TV, Cable TV, Wifi, Kitchen, Paid parking off...  
1  [Wifi, Wheelchair accessible, Kitchen, Free pa...  
2  [TV, Cable TV, Wifi, Air conditioning, Pool, K...  
3  [Internet, Wifi, Air conditioning, Kitchen, Bu...  
4  [TV, Cable TV, Internet, Wifi, Air conditionin...  

[5 rows x 50 columns]

In [56]:
file_path = r'C:\python\sd.csv'
merged_df.to_csv(file_path, index=False)